In [1]:
import os
BASE = '/Users/A124661/Documents/CS/CLOSE/xmls2/'

In [2]:
os.chdir('/Users/A124661/Documents/CS/CLOSE/output_files')

In [3]:
os.listdir(BASE)

['pubmed_xml_6.xml',
 'pubmed_xml_11.xml',
 'pubmed_xml_10.xml',
 'pubmed_xml_7.xml',
 'pubmed_xml_5.xml',
 'pubmed_xml_12.xml',
 'pubmed_xml_13.xml',
 'pubmed_xml_4.xml',
 'pubmed_xml_0.xml',
 'pubmed_xml_17.xml',
 'pubmed_xml_16.xml',
 'pubmed_xml_1.xml',
 'pubmed_xml_3.xml',
 'pubmed_xml_14.xml',
 'pubmed_xml_15.xml',
 'pubmed_xml_2.xml',
 'pubmed_xml_18.xml',
 'pubmed_xml_19.xml',
 'pubmed_xml_9.xml',
 'pubmed_xml_8.xml',
 'pubmed_xml_20.xml']

In [4]:
len(os.listdir(BASE))

21

In [5]:
import xml.etree.ElementTree as ET
import json
import csv
from typing import List

In [6]:
import xml.etree.ElementTree as ET
import json
import csv
from typing import List

def extract_data_to_dict(xml_filename: str) -> dict:
    tree = ET.parse(xml_filename)
    article_iterator = tree.iterfind(".//PubmedArticle")
    jsondict =  {}
    no_abstract_counter = 0
    no_meshheadingnode = 0
    no_meshheading_descriptornamenode = 0
    no_meshheading_qualifiernamenode = 0
    for article in article_iterator:
        medline_citation_node = article.find("MedlineCitation")
        article_node = medline_citation_node.find("Article")
        meshheadinglist_node = medline_citation_node.find("MeshHeadingList")
        if meshheadinglist_node is None:
            continue
        else:
            meshheading_node = meshheadinglist_node.find("MeshHeading")
        #for child in meshheading_node:
            #print(child.tag, child.text)
         


        
        
        if article_node.find("Abstract") is None:
            no_abstract_counter += 1
            continue
        
        if meshheadinglist_node.find("MeshHeading") is None:
            no_meshheadingnode +=1
            continue
        
        if meshheading_node.find("DescriptorName") is None:
            no_meshheading_descriptornamenode +=1
            continue
        
        if meshheading_node.find("QualifierName") is None:
            no_meshheading_qualifiernamenode +=1
            continue
        # TODO: remove this commented  code, we will just use pubdate
            # date_completed_node = medline_citation_node.find("DateCompleted")
            # if not date_completed_node:
            #     year_completed = None
            #     month_completed = None
            #     day_completed = None
            # else:
            #     year_completed = date_completed_node.find("Year").text
            #     month_completed = date_completed_node.find("Month").text
            #     day_completed = date_completed_node.find("Day").text


        pmid = medline_citation_node.find("PMID").text
        title = article_node.find("ArticleTitle").text
        abstract_text = article_node.find("Abstract").find("AbstractText").text
        mesh_descriptorname = meshheading_node.find("DescriptorName").text
        mesh_qualifiername = meshheading_node.find("QualifierName").text
        print("title: ", title)
        #print("mesh_descriptorname: ",mesh_descriptorname)
        #print("mesh_qualifiername: ", mesh_qualifiername)
        
        meshheading_list_node = medline_citation_node.find("MeshHeadingList")
        
        if meshheading_list_node is not None:
            meshheading_iterator = meshheading_list_node.iterfind("MeshHeading")
            mesh_descriptor_list = []
            mesh_qualifier_list = []
            for mesh in meshheading_iterator:
                descriptor = mesh.find("DescriptorName")
                qualifier = mesh.find("QualifierName")

                descriptor_text =  descriptor.text if descriptor is not None else None
                qualifier_text = qualifier.text if qualifier is not None else None
                
                mesh_descriptor_list.append(descriptor_text)
                mesh_qualifier_list.append(qualifier_text)

                #mesh_list.append({
                #    "DescriptorName": descriptor_text,
                #    "QualifierName": qualifier_text,
                #})
            #print("mesh_descriptor_list: ", mesh_descriptor_list)
            #print("mesh_qualifier_list: ", mesh_qualifier_list)
        
        
        
        #mesh_descriptorname = meshheadinglist_node.find("MeshHeading").find("DescriptorName").text
        #mesh_qualifiername = meshheadinglist_node.find("MeshHeading").find("QualifierName").text

        journal_node = article_node.find("Journal")
        journal_abbrev = journal_node.find("ISOAbbreviation").text

        # TODO: remove this commented code if above works
            # journal_info_node = article_node.find("Journal")
            # journal_abbrev = journal_info_node.find("ISOAbbreviation").text
        
        pub_date_node = journal_node.find("JournalIssue").find("PubDate")
        pub_year_node = pub_date_node.find("Year")
        if pub_year_node is None:
            medline_date_node = pub_date_node.find("MedlineDate")
            if  medline_date_node is None:
                pub_year = None
                print("No publication year for pmid:  ", pmid)
            else:
                pub_year = medline_date_node.text[:5]
        else:
            pub_year = pub_year_node.text

        author_list_node = article_node.find("AuthorList")
        if author_list_node is not None:
            author_iterator = author_list_node.iterfind("Author")
            author_list = []
            for author in author_iterator:

                ln = author.find("LastName")
                affiliation = author.find("AfilliationInfo")
                fn = author.find("ForeName")
                initials = author.find("Initials")

                initials_text =  initials.text if initials is not None else None
                affil_text = affiliation.text if affiliation is not None else None
                first_name = fn.text if fn is not None else None
                last_name = ln.text if ln is not None else None

                author_list.append({
                    "FirstName": first_name,
                    "LastName": last_name,
                    "Initials": initials_text,
                    "AffiliationInfo": affil_text
                })

                if ln is None:
                    collective_name_node = author.find("CollectiveName")
                    if collective_name_node is not None:
                        author_list[-1]["CollectiveName"] = collective_name_node.text
        else:
            author_list = None
        jsondict[pmid] = {
            "Title": title,
            "Authors": author_list,
            "Journal": journal_abbrev,
            "Abstract": abstract_text,
            "PMID": pmid,
            "PublicationYear": pub_year,
            "MeSHDescriptorName": mesh_descriptor_list,
            "MeSHQualifierName": mesh_qualifier_list
        }
    print("Articles with no Abstract: ", no_abstract_counter)
    return jsondict

def extract_many_xmls(base_name: str, max_number: int) ->  dict:
    big_dict = {}
    for i in range(max_number+1):
        print(i)
        curr_filename = "{0}_{1}.xml".format(base_name, str(i))
        big_dict.update(extract_data_to_dict(curr_filename))
    return big_dict

def dict_to_list_of_lists(jsondict: dict, debug: bool = False) -> List[List[str]]:
    csv_list = [["PMID", "Title",  "Journal", "Abstract", "PublicationYear", 
                 "MeSHDescriptorName", "MeSHQualifierName"]]
    noDateCounter =  0
    for pmid in jsondict:
        article_info = jsondict[pmid]
        if article_info["PublicationYear"] is None:
            noDateCounter += 1
        
        csv_list.append([
            article_info["PMID"],
            article_info["Title"],
            article_info["Journal"],
            article_info["Abstract"],
            article_info["PublicationYear"],
            article_info["MeSHDescriptorName"],
            article_info["MeSHQualifierName"]
        ])
    if debug:
        print("Articles with no date: ", noDateCounter)
    return csv_list

def json_to_list_of_lists(json_filename: str) ->  List[List[str]]:
    """Converts json file generated by previous methods into a list of lists
    with only the following fields:
        PMID, Title, Journal,  Abstract, Publication Year
    Arguments:
        json_filename {str} -- filename of the json encoded dictionary
        we want to convert. Should be in format [decriptor].json
    """
    with open(json_filename, "r") as json_file:
        jsondict = json.load(json_file)
    return dict_to_list_of_lists(jsondict)            

In [9]:
dir_download= '/Users/A124661/Documents/CS/CLOSE/output_files' 

In [10]:
if __name__ =="__main__":
    base_name = os.path.join(BASE,"pubmed_xml")
    big_dict = extract_many_xmls(base_name, 20)
    #big_dict=extract_data_to_dict(os.path.join(BASE, "articles_5.xml"))
    #json_filename = os.path.join(dir_download, "cyrene_xml_articles.xml_0.json")
    #big_dict=extract_data_to_dict(os.path.join(BASE, "cyrene_xml_articles.xml_0.xml"))
    json_filename = os.path.join(dir_download, "negative_articles.json")
    with open(json_filename,"w") as jsonfile:
        json.dump(big_dict, jsonfile)
      
    
    csv_filename = json_filename[:-5]+".csv"
    list_of_articles = json_to_list_of_lists(json_filename)
    with open(csv_filename, "w") as csv_file:
        writer = csv.writer(csv_file)
        writer.writerows(list_of_articles)

    print("Successfully Executed")
    

0
title:  Separation of shoot and floral identity in Arabidopsis.
title:  Apontic binds the translational repressor Bruno and is implicated in regulation of oskar mRNA translation.
title:  The homeobox gene Pitx2: mediator of asymmetric left-right signaling in vertebrate heart and gut looping.
title:  Mrj encodes a DnaJ-related co-chaperone that is essential for murine placental development.
title:  Expression of Bcl-2 protein is decreased in colorectal adenocarcinomas with microsatellite instability.
title:  Clinical and functional effects of mutations in the DAX-1 gene in patients with adrenal hypoplasia congenita.
title:  Targeted expression of toxic genes directed by pituitary hormone promoters: a potential strategy for adenovirus-mediated gene therapy of pituitary tumors.
title:  Transcriptional inhibition of stromelysin by interferon-gamma in normal human fibroblasts is mediated by the AP-1 domain.
title:  Raf signaling stimulates and represses the human collagen X promoter throu

In [13]:
BASE = '/Users/A124661/Documents/CS/CLOSE/cyrene_xml/'
dir_download= '/Users/A124661/Documents/CS/CLOSE/output_files/positives' 

if __name__ =="__main__":
    #base_name = os.path.join(BASE,"pubmed_xml")
    #big_dict = extract_many_xmls(base_name, 20)
    big_dict=extract_data_to_dict(os.path.join(BASE, "cyrene_xml_0.xml"))
    #json_filename = os.path.join(dir_download, "cyrene_xml_articles.xml_0.json")
    #big_dict=extract_data_to_dict(os.path.join(BASE, "cyrene_xml_articles.xml_0.xml"))
    json_filename = os.path.join(dir_download, "postive_articles.json")
    with open(json_filename,"w") as jsonfile:
        json.dump(big_dict, jsonfile)
      
    
    csv_filename = json_filename[:-5]+".csv"
    list_of_articles = json_to_list_of_lists(json_filename)
    with open(csv_filename, "w") as csv_file:
        writer = csv.writer(csv_file)
        writer.writerows(list_of_articles)

    print("Successfully Executed")

title:  Transactivation of C-reactive protein by IL-6 requires synergistic interaction of CCAAT/enhancer binding protein beta (C/EBP beta) and Rel p50.
title:  Genomic organization and promoter analysis of the mouse ADP-ribosylarginine hydrolase gene.
title:  Transcriptional regulation of the PXR gene: identification and characterization of a functional peroxisome proliferator-activated receptor alpha binding site within the proximal promoter of PXR.
title:  FOXO1 represses peroxisome proliferator-activated receptor-gamma1 and -gamma2 gene promoters in primary adipocytes. A novel paradigm to increase insulin sensitivity.
title:  Structure and expression of the Ah receptor repressor gene.
title:  Additive effect between NF-kappaB subunits and p53 protein for transcriptional activation of human p53 promoter.
title:  Transcription of the RelB gene is regulated by NF-kappaB.
title:  C/EBPalpha and C/EBPdelta activate the clara cell secretory protein gene through interaction with two adjace